In [1]:
## All minimum setup and librarries required

import numpy as np
import pandas as pd 

import os
for dirname, _, filenames in os.walk('/kaggle/input'):
    for filename in filenames:
        print(os.path.join(dirname, filename))

import tensorflow as tf
from tensorflow import keras
from tensorflow.keras.preprocessing.text import Tokenizer   ## Generate dictionary of word encodings
from tensorflow.keras.preprocessing.sequence import pad_sequences
print("Tensorflow - ",tf.__version__)

/kaggle/input/medium-articles-with-content/Medium_AggregatedData.csv
Tensorflow -  2.3.0


# Importing packages

In [2]:
import gensim
from gensim.utils import simple_preprocess
from gensim.parsing.preprocessing import STOPWORDS
from nltk.stem import WordNetLemmatizer, SnowballStemmer
from nltk.stem.porter import *

import numpy as np
np.random.seed(2018)
import nltk
nltk.download('wordnet')

[nltk_data] Downloading package wordnet to /usr/share/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


True

# Data input

In [3]:
path = "../input/medium-articles-with-content/Medium_AggregatedData.csv"
dataframe_full = pd.read_csv(path, error_bad_lines=False)
dataframe_imp = pd.read_csv(path, error_bad_lines=False)

In [4]:
dataframe_full.head()

audioVersionDurationSec codeBlock  codeBlockCount  collectionId  \
0                        0       NaN             0.0  638f418c8464   
1                        0       NaN             0.0  638f418c8464   
2                        0       NaN             0.0  638f418c8464   
3                        0       NaN             0.0           NaN   
4                        0       NaN             0.0           NaN   

  createdDate      createdDatetime firstPublishedDate firstPublishedDatetime  \
0  2018-09-18  2018-09-18 20:55:34         2018-09-18    2018-09-18 20:57:03   
1  2018-09-18  2018-09-18 20:55:34         2018-09-18    2018-09-18 20:57:03   
2  2018-09-18  2018-09-18 20:55:34         2018-09-18    2018-09-18 20:57:03   
3  2018-01-07  2018-01-07 17:04:37         2018-01-07    2018-01-07 17:06:29   
4  2018-01-07  2018-01-07 17:04:37         2018-01-07    2018-01-07 17:06:29   

   imageCount  isSubscriptionLocked  ...        slug        name postCount  \
0           1                 False  ...  blockchain  Blockchain  265164.0   
1           1                 False  ...     samsung     Samsung    5708.0   
2           1                 False  ...          it          It    3720.0   
3          13                 False  ...  technology  Technology  166125.0   
4          13                 False  ...    robotics    Robotics    9103.0   

         author  bio        userId    userName  usersFollowedByCount  \
0   Anar Babaev  NaN  f1ad85af0169  babaevanar                 450.0   
1   Anar Babaev  NaN  f1ad85af0169  babaevanar                 450.0   
2   Anar Babaev  NaN  f1ad85af0169  babaevanar                 450.0   
3  George Sykes  NaN  93b9e94f08ca    tasty231                   6.0   
4  George Sykes  NaN  93b9e94f08ca    tasty231                   6.0   

   usersFollowedCount scrappedDate  
0               404.0     20181104  
1               404.0     20181104  
2               404.0     20181104  
3                22.0     20181104  
4                22.0     20181104  

[5 rows x 50 columns]

# Checking the data

In [5]:
x = dataframe_full['name'][10]
y = dataframe_full['publicationdescription'][15]
print(x)
print(y)
print(dataframe_full.shape)
print(dataframe_full['name'][10])
print(dataframe_full['name'][11])
print(dataframe_full['name'][12])
print(dataframe_full['title'][10])

Big Data Training Mumbai
Non-obvious meditation advice from people on the battlefront of daily creation
(279577, 50)
Big Data Training Mumbai
Robotics
Meditation
Ascent of data Science, SAS and Big data Analyst Trainings Programs


# Adding a column with indices

In [6]:
dataframe_full['index'] = dataframe_full.index

# Reducing the columns to required columns

In [7]:
data_min = dataframe_full.drop(['audioVersionDurationSec', 'codeBlock', 'codeBlockCount',
       'collectionId', 'createdDate', 'createdDatetime', 'firstPublishedDate',
       'firstPublishedDatetime', 'imageCount', 'isSubscriptionLocked',
       'language', 'latestPublishedDate', 'latestPublishedDatetime',
       'linksCount', 'postId', 'readingTime', 'recommends',
       'responsesCreatedCount', 'socialRecommendsCount','tagsCount','totalClapCount', 'uniqueSlug',
       'updatedDate', 'updatedDatetime', 'url', 'vote', 'wordCount',
       'publicationdescription', 'publicationdomain',
       'publicationfacebookPageName', 'publicationfollowerCount',
       'publicationname', 'publicationpublicEmail', 'publicationslug',
       'publicationtags', 'publicationtwitterUsername', 'tag_name', 'slug',
       'name', 'postCount', 'author', 'bio', 'userId', 'userName',
       'usersFollowedByCount', 'usersFollowedCount', 'scrappedDate'], axis=1)

In [8]:
data_min.head()

subTitle  \
0  A major private IT company implements blockcha...   
1  A major private IT company implements blockcha...   
2  A major private IT company implements blockcha...   
3                                       Introduction   
4                                       Introduction   

                                                text  \
0  Private Business, Government and Blockchain\n\...   
1  Private Business, Government and Blockchain\n\...   
2  Private Business, Government and Blockchain\n\...   
3  EPQ draft 1 (4844 words)\nhttps://upload.wikim...   
4  EPQ draft 1 (4844 words)\nhttps://upload.wikim...   

                                         title  index  
0  Private Business, Government and Blockchain      0  
1  Private Business, Government and Blockchain      1  
2  Private Business, Government and Blockchain      2  
3                     EPQ draft 1 (4844 words)      3  
4                     EPQ draft 1 (4844 words)      4

**There are ~300000 entries**

# Another version of reduced columns

In [9]:
print(dataframe_full.columns)

Index(['audioVersionDurationSec', 'codeBlock', 'codeBlockCount',
       'collectionId', 'createdDate', 'createdDatetime', 'firstPublishedDate',
       'firstPublishedDatetime', 'imageCount', 'isSubscriptionLocked',
       'language', 'latestPublishedDate', 'latestPublishedDatetime',
       'linksCount', 'postId', 'readingTime', 'recommends',
       'responsesCreatedCount', 'socialRecommendsCount', 'subTitle',
       'tagsCount', 'text', 'title', 'totalClapCount', 'uniqueSlug',
       'updatedDate', 'updatedDatetime', 'url', 'vote', 'wordCount',
       'publicationdescription', 'publicationdomain',
       'publicationfacebookPageName', 'publicationfollowerCount',
       'publicationname', 'publicationpublicEmail', 'publicationslug',
       'publicationtags', 'publicationtwitterUsername', 'tag_name', 'slug',
       'name', 'postCount', 'author', 'bio', 'userId', 'userName',
       'usersFollowedByCount', 'usersFollowedCount', 'scrappedDate', 'index'],
      dtype='object')


The required columns are:
* language
* subTitle
* tagsCount
* text
* title
* url
* wordCount
* publicationdescription
* tag_name
* name

In [10]:
required_col = ['language','subTitle','tagsCount','text','title','url','wordCount','publicationdescription'
               ,'tag_name','name']

# Initializing the stemmer

In [11]:
stemmer = SnowballStemmer("english")

# Perform lemmatization and stem preprocessing steps on the data set.

In [12]:

def lemmatize_stemming(text):
    return stemmer.stem(WordNetLemmatizer().lemmatize(text, pos='v'))
def preprocess(text):
    result = []
    for token in gensim.utils.simple_preprocess(text):
        if token not in gensim.parsing.preprocessing.STOPWORDS and len(token) > 3:
            result.append(lemmatize_stemming(token))
    return result

# Checking the pre process

In [13]:
doc_sample = data_min[data_min['index'] == 4310].values[0][2]
print('original document: ')
words = []
for word in doc_sample.split(' '):
    words.append(word)
print(words)
print('\n\n tokenized and lemmatized document: ')
print(preprocess(doc_sample))

original document: 
['Info', '201', 'and', 'R:', 'What', 'Should', 'I', 'Expect?']


 tokenized and lemmatized document: 
['info', 'expect']


# Processed docs

In [14]:
title_list = data_min['title'].astype(str)   ## using astype(str) eliminates the floting type error
title_list.describe()

count                          279577
unique                          70276
top       10 new things to read in AI
freq                              186
Name: title, dtype: object

In [15]:
processed_docs = title_list.map(preprocess)
processed_docs[:10]

0                   [privat, busi, govern, blockchain]
1                   [privat, busi, govern, blockchain]
2                   [privat, busi, govern, blockchain]
3                                        [draft, word]
4                                        [draft, word]
5                                        [draft, word]
6                                        [draft, word]
7    [ascent, data, scienc, data, analyst, train, p...
8    [ascent, data, scienc, data, analyst, train, p...
9    [ascent, data, scienc, data, analyst, train, p...
Name: title, dtype: object

# Above we get a tokenised list

In [16]:
article_titles = dataframe_full['title']
art_grp_1 = article_titles[16:25]
print(art_grp_1)
print(dataframe_full.language.unique())

16                  2017 Big Data, AI and IOT Use Cases
17                  2017 Big Data, AI and IOT Use Cases
18                  2017 Big Data, AI and IOT Use Cases
19                  2017 Big Data, AI and IOT Use Cases
20                  2017 Big Data, AI and IOT Use Cases
21    Oracle จึงขอเชิญชาวไอทีทั้งหลายเข้าร่วมงาน Ora...
22    Oracle จึงขอเชิญชาวไอทีทั้งหลายเข้าร่วมงาน Ora...
23    Oracle จึงขอเชิญชาวไอทีทั้งหลายเข้าร่วมงาน Ora...
24    Oracle จึงขอเชิญชาวไอทีทั้งหลายเข้าร่วมงาน Ora...
Name: title, dtype: object
['en' 'th' 'ja' 'zh' 'ru' 'pt' 'es' 'zh-Hant' 'id' 'my' 'de' 'tr' 'fr'
 'ko' 'it' 'lo' 'un' 'vi' 'cs' 'sk' 'is' 'sv' 'bn' 'mn' 'da' 'no' 'bg'
 'ar' 'pl' 'nl' 'ro' 'ca' 'hu' 'hi' 'ka' 'el' 'ms' 'uk' 'si' 'sr' 'lt'
 'la' 'fa' 'ml' 'sl' 'mr' 'az' 'lv' 'te' 'mk' 'nn' 'fi']


In [17]:
english_titles = dataframe_full[dataframe_full['language'] == 'en']
english_titles.head()
print(english_titles.shape)

(257655, 51)


In [18]:
print(dataframe_imp.shape)
dataframe_imp.dropna(how = 'all')
print(dataframe_imp.shape)

(279577, 50)
(279577, 50)


So thing is missing in any rows

In [19]:
dataframe_imp.drop(dataframe_imp[dataframe_imp['language'] != 'en'].index, inplace = True)

In [20]:
dataframe_imp.shape

(257655, 50)

In [21]:
dataframe_full.shape

(279577, 51)

after dropping all the non english rows

In [22]:
dataframe_imp['language'].unique()

array(['en'], dtype=object)

In [23]:
dataframe_imp = dataframe_imp[required_col]
dataframe_imp.shape

(257655, 10)

after dropping all non essential columns `dataframe_imp` is the required dataframe

In [24]:
title_list = dataframe_imp['title'].astype(str)   ## using astype(str) eliminates the floting type error
title_list.describe()
# title_list.to_numpy()

count                          257655
unique                          64417
top       10 new things to read in AI
freq                              186
Name: title, dtype: object

### Word Tokenization

In [25]:
tokenizer = Tokenizer(num_words = 100, oov_token= '<OOV>')  ## Select top 100 words
tokenizer.fit_on_texts(title_list)
word_index = tokenizer.word_index        ## return a dictionary
print(word_index)

{'<OOV>': 1, 'the': 2, 'to': 3, 'of': 4, 'and': 5, 'ai': 6, 'in': 7, 'a': 8, 'data': 9, 'learning': 10, 'for': 11, '—': 12, 'with': 13, 'how': 14, 'machine': 15, 'is': 16, 'intelligence': 17, 'artificial': 18, 'on': 19, 'your': 20, 'science': 21, 'what': 22, 'using': 23, '2018': 24, 'you': 25, 'part': 26, 'from': 27, 'deep': 28, 'why': 29, 'future': 30, 'i': 31, 'an': 32, 'can': 33, 'are': 34, 'new': 35, 'will': 36, '1': 37, 'it': 38, 'at': 39, 'python': 40, '2': 41, 'we': 42, 'about': 43, 'neural': 44, 'by': 45, 'be': 46, '3': 47, '5': 48, 'my': 49, 'technology': 50, 'world': 51, 'business': 52, 'tech': 53, 'blockchain': 54, 'that': 55, 'our': 56, 'analysis': 57, 'google': 58, 'human': 59, 'big': 60, 'analytics': 61, '4': 62, 'do': 63, 'not': 64, 'networks': 65, 'as': 66, 'or': 67, 'ml': 68, 'digital': 69, '2017': 70, 'time': 71, 'first': 72, 'use': 73, 'chatbots': 74, 'building': 75, 'should': 76, 'week': 77, 'network': 78, '10': 79, 'make': 80, 'need': 81, 'top': 82, 'into': 83, 'th

All unknown words are represented as 1

### Text to sequence

In [26]:
sequences = tokenizer.texts_to_sequences(title_list)
print(sequences)

[[1, 52, 1, 5, 54], [1, 52, 1, 5, 54], [1, 52, 1, 5, 54], [1, 1, 37, 1, 1], [1, 1, 37, 1, 1], [1, 1, 37, 1, 1], [1, 1, 37, 1, 1], [1, 4, 9, 21, 1, 5, 60, 9, 1, 1, 1], [1, 4, 9, 21, 1, 5, 60, 9, 1, 1, 1], [1, 4, 9, 21, 1, 5, 60, 9, 1, 1, 1], [1, 4, 9, 21, 1, 5, 60, 9, 1, 1, 1], [33, 8, 1, 1, 1, 1, 1, 1, 59, 33], [33, 8, 1, 1, 1, 1, 1, 1, 59, 33], [33, 8, 1, 1, 1, 1, 1, 1, 59, 33], [33, 8, 1, 1, 1, 1, 1, 1, 59, 33], [33, 8, 1, 1, 1, 1, 1, 1, 59, 33], [70, 60, 9, 6, 5, 1, 73, 1], [70, 60, 9, 6, 5, 1, 73, 1], [70, 60, 9, 6, 5, 1, 73, 1], [70, 60, 9, 6, 5, 1, 73, 1], [70, 60, 9, 6, 5, 1, 73, 1], [18, 17, 16, 2, 1, 1], [1, 1, 1, 1, 11, 28, 10, 1], [1, 1, 1, 1, 11, 28, 10, 1], [1, 1, 1, 1, 11, 28, 10, 1], [1, 1, 1, 1, 11, 28, 10, 1], [1, 1, 1, 1, 11, 28, 10, 1], [6, 5, 1, 1, 19, 2, 51], [2, 1, 87, 5, 1, 1, 87, 4, 28, 10], [2, 1, 87, 5, 1, 1, 87, 4, 28, 10], [2, 1, 87, 5, 1, 1, 87, 4, 28, 10], [2, 1, 87, 5, 1, 1, 87, 4, 28, 10], [82, 79, 1, 11, 2, 9, 21, 1, 3, 1], [82, 79, 1, 11, 2, 9, 21, 1, 

### Padding (to bring uniformity to the text sequences)

In [27]:
padded = pad_sequences(sequences, padding='post', maxlen = 15, truncating ='post')  ## Zeros will be 
                                                                                  ## added before the sequence
print(padded[1])

[ 1 52  1  5 54  0  0  0  0  0  0  0  0  0  0]


**example of a padded tokenized text sequence**